In [1]:
import math
import numpy as np

# Elliptical, parabolic, and hyperbolic orbits using the Euler method

In the simple_two_body.ipynb notebook I implemented circular orbits with arbitary starting positions and confirmed that the truncation error converged linearly with timestep for the Euler method.  

In this notebook I plan to implement hyperbolic, elliptical, and parabolic orbits using the Euler method. Parabolic orbits are marginally bound, hyperbolic orbits are unbound, and elliptical orbits are bound but oblong. All orbits should have the center of mass at one focus for both stars orbit and be symmetric between the two stars. 

Elliptical orbits should be elongated away from the other star. 

Hyperbolic and parabolic orbits should open away from the other star. 

All orbits should conserve energy and angular momentum. Later this could be enforced. I will probably not do that in this notebook. 

It would be meaningless to evaluate the L0 error for a hyperbolic or parabolic orbit since there is no cycle and the L0 error is found after one or more cycles when the system returns to its starting point. However, it would be possible to evaluate it for the elliptical orbit system, and I intend to check that the convergence of the L0 error with dt is linear as it should be for the Euler method. 

Because the convergence can be tested for ellipses only and because ellipses are closed so make it clear if they are not working correctly graphically, I will begin with ellipses then proceed to parabolas and hyperbolas. 

# Conic sections

Circles, ellipses, parabolas, and hyperbolas are called conic sections because they can all be obtained by taking slices of an infinite cone. 

Conic sections are related to each other through a parameter called eccentricity. Circles have an eccentricity of 0. Ellipses have an eccentricity of 0<e<1. Parabolas have an eccentricity of e=1. Hyperbolas have an eccentricity of e>1. 

Circles are described by the equation x^2+y^2=r^2 where r is the radius. They can also be described parametrically using sine and cosine. That is done below. 

In [2]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
radius=10
t=2*math.pi*0.01*np.arange(103)
centerx=3
centery=5
p = figure(title="Circle", plot_width=400, plot_height=400)
p.line(centerx+np.cos(t),centery+np.sin(t),line_width=3,line_color="blue",legend="Circle")
p.circle(centerx,centery,line_width=15,line_color="green",legend="Center")
p.legend.location="bottom_right"
show(p)

Loading BokehJS ...

Ellipses are shaped like ovals. They have two locations called focuses that determine their shapes. If a string were connected to both focuses, which are inside the ellipse, you could slide a pencil along the string and draw the ellipse keeping the string taut. The two focuses and the ellipse form a triangle with hypoteneuses of fixed length. 

Half the shorter of the two widths of the ellipse is called the semimajor axis, a. It's like a radius for ellipses. The lenght of the longer width is (1+e)*a. The focus is offset from the center by f=e*sqrt(1-e^2)*a. 

Ellipses can also be drawn at angles to the axis. An ellipse aligned with the x and y axis is shown below. 

The nonparametric equation for an ellipse is x^2/a^2+y^2/b^2=1
Below the ellipse is described parametrically. 

In [3]:
def getfocus(a,ecc):
    b=a*(1+ecc)
    return np.sqrt(b**2-a**2)

In [4]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
radius=10
t=2*math.pi*0.01*np.arange(103)
a=10
ecc=.5
b=a*(1+ecc)
centerx=0
centery=0
focusx=centerx+getfocus(a,ecc)
focusy=centery+0.0
p = figure(title="Ellipse", plot_width=400, plot_height=400, x_range=[-15,15], y_range=[-15,15])
p.line(centerx+b*np.cos(t),centery+a*np.sin(t),line_width=3,line_color="blue",legend="Circle")
p.circle(focusx,focusy,line_width=15,line_color="green",legend="Focus 1")
p.circle(centerx-getfocus(a,ecc),focusy, line_width=15, line_color="red", legend="Focus 2")
p.legend.location="bottom_right"
show(p)

Loading BokehJS ...

In [5]:
import numpy as np
import matplotlib.pyplot as plt

def NewtonianForce(mass1,mass2, r):
    return (6.67408*10**-11)*mass1*mass2/r/r;

In [6]:
def euler(h,t, x,y,z,f,debugprint):
    xstep = (f(t, x, y,z)+f(t+h,x+h,y,z))/2*h
    xnew=x+xstep
    if(debugprint):
        print(h,t,x,xstep,xnew)
    return t+h,xnew

In [7]:
import math
def InitialDataEqualMassConic(radius,ecc,angle,initmass):
    orbitalangle=angle
    print("angle",angle)
    phi=np.array([math.pi+orbitalangle,orbitalangle])
    orbitalradius=radius*np.ones(2) #semimajor axis
    eccentricity=ecc
    print(eccentricity)
    mass=np.ones(2)
    masses=initmass*mass #*masssun (natural units)
    return phi,orbitalangle,orbitalradius,eccentricity, masses
    

In [8]:
import random,numpy as np
rad0=100
ecc0=0.3
angle0=0.0
mass0=1.0
initdateqellipse=InitialDataEqualMassConic(rad0,ecc0,angle0,mass0)
print(initdateqellipse)

angle 0.0
0.3
(array([3.14159265, 0.        ]), 0.0, array([100., 100.]), 0.3, array([1., 1.]))


In [9]:
def getxyuveqtwoellipses(initdat):
    phi,orbitangle,orbitalradius,eccentricity, masses=initdat
    print("initdat", orbitalradius, phi, np.cos(phi), np.sin(phi))
    metersperAU=1
    Gconstant=1
    #fix x0 y0 at one star, disregard initial data, use orbital radius as separation between stars
    #this is consistant with choice in previous part
    cosphi=np.cos(phi)
    sinphi=np.sin(phi)
    coordsep=orbitalradius #/2.
    print("coordsep",coordsep)
    #x0=orbitalradius/2.*np.cos(phi)*metersperAU
    #y0=orbitalradius/2.*np.sin(phi)*metersperAU
    count=0
    for phi0 in phi:
        if phi0==0:
            print("zero")
            #x0[count]=orbitalradius[count]/2.
            #y0[count]=0
            cosphi[count]=1.0
            sinphi[count]=0.0
        if phi0==math.pi:
            cosphi[count]=-1.0
            sinphi[count]=0.0
            print("pi")
            #x0[count]=-orbitalradius[count]/2.
            #y0[count]=0
        if phi0==math.pi/2.:
            cosphi[count]=0.0
            sinphi[count]=1.0
            #x0[count]=0
            #y0[count]=orbitalradius[count]/2.
        if phi0==3*math.pi/2.:
            cosphi[count]=0.0
            sinphi[count]=-1.0
            #x0[count]=0
            #y0[count]=-orbitalradius[count]/2.
        count+=1
    x0=coordsep*cosphi
    y0=coordsep*sinphi
    #x0[1]=0.0
    #y0[1]=0.0
    z0=np.zeros(2)
    print(x0)
    print(y0)
    v=np.zeros(2)
    a=np.zeros(2)
    ux0=0.
    uy0=0.
    uz0=0.
    ax0=0.
    ay0=0.
    az0=0.
    vx0=0.
    vy0=0.
    vz0=0.
    print(eccentricity)
    #masses=np.zeros(2)
    #masses[0]=masses[1]+masses[0]
    #masses[1]=(masses[1]*masses[0])/(masses[1]+masses[0])
    if eccentricity<1 and eccentricity>0:
        #elliptical
        orbitalr=orbitalradius[0]/2. #reduced mass
        focusdisp=getfocus(orbitalr,eccentricity) #displacement of the center due to the focus being at the center
        coordsep=orbitalr*(1+eccentricity) #start at aphelion
        starsep=2.*coordsep #two stars, at opposite ends of the orbit
        Fapastron=masses[1]*masses[0]/starsep**2
        x0=(coordsep+focusdisp)*cosphi
        y0=(coordsep+focusdisp)*sinphi
        x0[0]=0.0
        y0[0]=0.0
        v=np.zeros(2)
        v=np.sqrt(masses[1]*masses[0]*(2./starsep-1./(2.*orbitalr)/masses)) 
        ux0=-v[0]*sinphi
        uy0=v[1]*cosphi #initial data in y only 
        uz0=np.zeros(2)
    
        a=np.zeros(2)
        a=Fapastron/masses
    
        ax0=-a[0]*cosphi
        ay0=-a[1]*sinphi
        az0=np.zeros(2)
    elif eccentricity[0]==0.0: #circular
        #start at perihelion for both (eliptical, doesn't generalize to three body)
        #actually start with circular orbit
        ux0=np.zeros(2) #*149597870700
        #centrepital force balances gravitational force
        metersperAU=1 #natural units
        #G=1
        Gconstant=1
        #Fcentripital=mass1*v**2/rphys
        #centF=accel
        #Faccel=G*m1*m2/r^2
        r0=2.*orbitalradius #Mystery factor of 2
        print("r0", r0)
        v=np.zeros(2)
        for i in np.arange(2):
            v[i]=np.sqrt(Gconstant*masses[(i+1)%2]/np.abs(r0[i]))
        print(v)
        #r0=orbitalradius #np.sqrt(x0**2+y0**2)
        ux0=-v[0]*sinphi
        uy0=v[1]*cosphi #initial data in y only 
        uz0=np.zeros(2)
    
        a=np.zeros(2)
        a=Fapastron/masses
    
        ax0=-a[0]*cosphi
        ay0=-a[1]*sinphi
        az0=np.zeros(2)

    
    
    return masses,x0,y0,z0, ux0, uy0,uz0, ax0, ay0,az0

In [10]:
xyuvaeqtwoellipses=getxyuveqtwoellipses(initdateqellipse)
print(xyuvaeqtwoellipses)

initdat [100. 100.] [3.14159265 0.        ] [-1.  1.] [1.2246468e-16 0.0000000e+00]
coordsep [100. 100.]
pi
zero
[-100.  100.]
[0. 0.]
0.3
(array([1., 1.]), array([  0.        , 106.53311931]), array([0., 0.]), array([0., 0.]), array([-0., -0.]), array([-0.07337994,  0.07337994]), array([0., 0.]), array([ 5.91715976e-05, -5.91715976e-05]), array([-0., -0.]), array([0., 0.]))


In [43]:
def timestep(step,t,dt,mtotal, mass,xi,yi,zi, vxi, vyi, vzi, axi, ayi, azi):
    xii=np.zeros(np.size(xi))
    vxii=np.zeros(np.size(vxi))
    yii=np.zeros(np.size(yi))
    vyii=np.zeros(np.size(vyi))
    zii=np.zeros(np.size(vzi))
    vzii=np.zeros(np.size(vzi))
    rii=np.zeros(np.size(xi))
    axii=np.zeros(np.size(axi))
    ayii=np.zeros(np.size(ayi))
    azii=np.zeros(np.size(azi))
    
    #This is redundant in the center of mass system
    Gconstant=6.408*10**-11
    Gconstant=1
    for k in np.arange(len(rii)):
        for j in np.arange(len(rii)):
            if j!=k:
                rreljk=np.abs((xi[j] - xi[k])**2+(yi[j]-yi[k])**2+(zi[j]-zi[k])**2)**(1./2.)
                #print(rreljk)
                axii[j]-=Gconstant*mass[k]*(xi[j]  - xi[k])/rreljk**3
                ayii[j]-=Gconstant*mass[k]*(yi[j]  - yi[k])/rreljk**3
                azii[j]-=Gconstant*mass[k]*(zi[j]  - zi[k])/rreljk**3
    #print(xii)
    Energy=0
    L=np.zeros(len(x))
    p=0.
    for m in np.arange(len(x)):
        #m represents choices of mass
        i=step
        
        xii[m] = xi[m] + dt*vxi[m]
        vxii[m] = vxi[m] + dt*axi[m]
        yii[m]= yi[m] + dt*vyi[m]
        vyii[m] = vyi[m] + dt*ayi[m]
        zii[m]= zi[m] + dt*vzi[m]
        vzii[m] = vzi[m] + dt*azi[m]
        rii[m]=np.sqrt(xi[m]**2+yi[m]**2+zi[m]**2)
        
        #print(vyii[m],vyi[m],ayi[m],dt)
        #print(yii[m],yi[m],vyi[m],dt)
        Energy+=1/2.*mass[m]*(vxii[m]**2+vyii[m]**2+vzii[m]**2)
        for j in np.arange(len(x)):
            if j!=m:
                rreljm=np.abs((xii[j] - xii[m])**2+(yii[j]-yii[m])**2+(zii[j]-zii[m])**2)**(1./2.)
                #print(rreljk)
                Energy-=mass[m]*mass[j]/rreljm
                xrel=xii[j]-xii[m]
                yrel=yii[j]-yii[m]
                zrel=zii[j]-zii[m]
                L[m]+=mass[m]*(vxii[m]*(yrel-zrel)+vyii[m]*(-xrel+zrel)+vzii[m]*(xrel-yrel))
    
    print(L)    
    return mass, xii,yii,zii,vxii,vyii,vzii,axii,ayii,azii, Energy, L
                    

In [44]:
dt=1 #*31556926 #seconds per year
numsteps=10000
mass0,x,y,z0,vx,vy,vz0,ax,ay,az0=xyuvaeqtwoellipses
print(x)
xcoord1=[]
xcoord2=[]
ycoord1=[]
ycoord2=[]
vxarr1=[]
vxarr2=[]
vyarr1=[]
vyarr2=[]
Earr=[]
Larr=[]
t=0.0
tarr=[]
masstotal=1.
for i in np.arange(1,numsteps):
    mass, x,y,z,vx,vy,vz,ax,ay,az,E,L=timestep(i,t,dt,masstotal,mass0,x,y,z0,vx,vy,vz0,ax,ay,az0)
    print(x,y,vx,vy,ax,ay,E,L)
    #print(ay) #forces should be equal and opposite, but in reduced mass framework accelerations are also equal and opposite
    #accelerations should evolve from y to x with time in a sinusoidal manner even in reduced mass framework
    #print(ax)
    t+=dt
    xcoord1.append(x[0])
    xcoord2.append(x[1])
    ycoord1.append(y[0])
    ycoord2.append(y[1])
    vxarr1.append(vx[0])
    vxarr2.append(vx[1])
    vyarr1.append(vy[0])
    vyarr2.append(vy[1])
    Earr.append(E)
    Larr.append(L[0])
    tarr.append(t)
#mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(2,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
#print(x,y,vx,vy,ax,ay) 
#mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(3,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
#print(x,y,vx,vy,ax,ay) 
#mass, x,y,z,vx,vy,vz,ax,ay,az=timestep(4,0,dt,mass,x,y,z,vx,vy,vz,ax,ay,az)
#print(x,y,vx,vy,ax,ay) 

[  0.         106.53311931]
[4.34200820e-06 7.81740244e+00]
[  0.         106.53311931] [-0.07337994  0.07337994] [ 5.91715976e-05 -5.91715976e-05] [-0.07337994  0.07337994] [ 8.81111183e-05 -8.81111183e-05] [0. 0.] -13.631705001866235 [4.34200820e-06 7.81740244e+00]
[1.72731851e-05 7.81742830e+00]
[5.91715976e-05 1.06533060e+02] [-0.14675988  0.14675988] [ 0.00014728 -0.00014728] [-0.07337994  0.07337994] [ 8.81108674e-05 -8.81108674e-05] [ 1.21381409e-07 -1.21381409e-07] -6.817852974861815 [1.72731851e-05 7.81742830e+00]
[3.66699203e-05 7.81745416e+00]
[2.06454314e-04 1.06532913e+02] [-0.22013982  0.22013982] [ 0.00023539 -0.00023539] [-0.07337982  0.07337982] [ 8.81103107e-05 -8.81103107e-05] [ 2.42761553e-07 -2.42761553e-07] -4.546567683646254 [3.66699203e-05 7.81745416e+00]
[6.25321336e-05 7.81748002e+00]
[4.41847897e-04 1.06532677e+02] [-0.29351963  0.29351963] [ 0.0003235 -0.0003235] [-0.07337957  0.07337957] [ 8.81095439e-05 -8.81095439e-05] [ 3.64140167e-07 -3.64140167e-07] -3

[  0.82586578 105.70725353] [-10.0757347  10.0757347] [ 0.01203961 -0.01203961] [-0.07225611  0.07225611] [ 8.61254983e-05 -8.61254983e-05] [ 1.64253516e-05 -1.64253516e-05] -0.10291404061714901 [0.06163405 7.8209374 ]
[0.06252181 7.82096309]
[  0.83790539 105.69521392] [-10.14799082  10.14799082] [ 0.01212573 -0.01212573] [-0.07223969  0.07223969] [ 8.60969331e-05 -8.60969331e-05] [ 1.65423032e-05 -1.65423032e-05] -0.1022048591627937 [0.06252181 7.82096309]
[0.0634158  7.82098877]
[  0.85003113 105.68308819] [-10.22023051  10.22023051] [ 0.01221183 -0.01221183] [-0.07222315  0.07222315] [ 8.60681703e-05 -8.60681703e-05] [ 1.66591917e-05 -1.66591917e-05] -0.10150582684750163 [0.0634158  7.82098877]
[0.06431602 7.82101445]
[  0.86224296 105.67087636] [-10.29245366  10.29245366] [ 0.0122979 -0.0122979] [-0.07220649  0.07220649] [ 8.60392099e-05 -8.60392099e-05] [ 1.67760167e-05 -1.67760167e-05] -0.1008167277304878 [0.06431602 7.82101445]
[0.06522246 7.82104012]
[  0.87454086 105.65857846

[  2.68056331 103.852556  ] [-17.97037588  17.97037588] [ 0.02138249 -0.02138249] [-0.06973536  0.06973536] [ 8.17934148e-05 -8.17934148e-05] [ 2.89316412e-05 -2.89316412e-05] -0.05903187909976601 [0.19732133 7.82376859]
[0.19887506 7.82379388]
[  2.7019458  103.83117351] [-18.04011124  18.04011124] [ 0.02146428 -0.02146428] [-0.06970643  0.06970643] [ 8.17442206e-05 -8.17442206e-05] [ 2.90391507e-05 -2.90391507e-05] -0.05881421313043961 [0.19887506 7.82379388]
[0.20043452 7.82381916]
[  2.72341009 103.80970923] [-18.10981767  18.10981767] [ 0.02154603 -0.02154603] [-0.06967739  0.06967739] [ 8.16948546e-05 -8.16948546e-05] [ 2.91465543e-05 -2.91465543e-05] -0.05859829143689006 [0.20043452 7.82381916]
[0.2019997  7.82384444]
[  2.74495612 103.7881632 ] [-18.17949507  18.17949507] [ 0.02162772 -0.02162772] [-0.06964825  0.06964825] [ 8.16453173e-05 -8.16453173e-05] [ 2.92538519e-05 -2.92538519e-05] -0.05838409325234534 [0.2019997  7.82384444]
[0.20357059 7.82386972]
[  2.76658384 103.76

[0.40553132 7.82656966]
[  5.57159187 100.96152745] [-25.57709427  25.57709427] [ 0.03020032 -0.03020032] [-0.06585283  0.06585283] [ 7.52865925e-05 -7.52865925e-05] [ 4.02440583e-05 -4.02440583e-05] -0.04219165032949427 [0.40553132 7.82656966]
[0.40768733 7.82659435]
[  5.60179218 100.93132713] [-25.6429471  25.6429471] [ 0.0302756 -0.0302756] [-0.06581258  0.06581258] [ 7.52201199e-05 -7.52201199e-05] [ 4.03378425e-05 -4.03378425e-05] -0.042088608519863485 [0.40768733 7.82659435]
[0.40984833 7.82661904]
[  5.63206779 100.90105153] [-25.70875968  25.70875968] [ 0.03035083 -0.03035083] [-0.06577224  0.06577224] [ 7.51535121e-05 -7.51535121e-05] [ 4.04314893e-05 -4.04314893e-05] -0.04198614112443893 [0.40984833 7.82661904]
[0.41201431 7.82664372]
[  5.66241861 100.8707007 ] [-25.77453193  25.77453193] [ 0.03042598 -0.03042598] [-0.06573181  0.06573181] [ 7.50867693e-05 -7.50867693e-05] [ 4.05249984e-05 -4.05249984e-05] -0.041884243407570715 [0.41201431 7.82664372]
[0.41418528 7.8266684 

[0.67363926 7.82927029]
[ 9.36794341 97.16517591] [-32.62111418  32.62111418] [ 0.03812348 -0.03812348] [-0.06084485  0.06084485] [ 6.71629674e-05 -6.71629674e-05] [ 4.97725669e-05 -4.97725669e-05] -0.03345071242653962 [0.67363926 7.82927029]
[0.67630244 7.82929422]
[ 9.40606689 97.12705243] [-32.68195903  32.68195903] [ 0.03819064 -0.03819064] [-0.06079508  0.06079508] [ 6.70837121e-05 -6.70837121e-05] [ 4.98499866e-05 -4.98499866e-05] -0.033390894088484814 [0.67630244 7.82929422]
[0.67896975 7.82931815]
[ 9.44425753 97.08886179] [-32.74275411  32.74275411] [ 0.03825773 -0.03825773] [-0.06074523  0.06074523] [ 6.70043624e-05 -6.70043624e-05] [ 4.99272509e-05 -4.99272509e-05] -0.033331333135771996 [0.67896975 7.82931815]
[0.68164116 7.82934207]
[ 9.48251526 97.05060406] [-32.80349934  32.80349934] [ 0.03832473 -0.03832473] [-0.0606953  0.0606953] [ 6.69249188e-05 -6.69249188e-05] [ 5.00043598e-05 -5.00043598e-05] -0.033272027941490534 [0.68164116 7.82934207]
[0.68431668 7.82936599]
[ 9

...

[128.00419744 -21.47107813] [-3.26248051  3.26248051] [ 0.00316688 -0.00316688] [ 0.05316958 -0.05316958] [-4.46290471e-05  4.46290471e-05] [ 1.98000067e-06 -1.98000067e-06] -0.011656379203889254 [6.81626092 7.96820095]
[6.81637114 7.96821046]
[128.00736432 -21.47424501] [-3.20931094  3.20931094] [ 0.00312225 -0.00312225] [ 0.05317156 -0.05317156] [-4.46294064e-05  4.46294064e-05] [ 1.94818264e-06 -1.94818264e-06] -0.011656260991796175 [6.81637114 7.96821046]
[6.81647967 7.96821998]
[128.01048658 -21.47736726] [-3.15613938  3.15613938] [ 0.00307762 -0.00307762] [ 0.05317351 -0.05317351] [-4.4629751e-05  4.4629751e-05] [ 1.91636615e-06 -1.91636615e-06] -0.011656144157532796 [6.81647967 7.96821998]
[6.81658651 7.9682295 ]
[128.0135642  -21.48044489] [-3.10296587  3.10296587] [ 0.00303299 -0.00303299] [ 0.05317542 -0.05317542] [-4.4630081e-05  4.4630081e-05] [ 1.88455119e-06 -1.88455119e-06] -0.01165602870094598 [6.81658651 7.9682295 ]
[6.81669165 7.96823901]
[128.01659719 -21.48347788] [

[128.08326859 -21.55014927] [ 2.64438104 -2.64438104] [-0.00178591  0.00178591] [ 0.05319541 -0.05319541] [-4.45801673e-05  4.45801673e-05] [-1.54394299e-06  1.54394299e-06] -0.011651645345447603 [6.81816432 7.96925592]
[6.81808683 7.96926541]
[128.08148268 -21.54836337] [ 2.69757645 -2.69757645] [-0.00183049  0.00183049] [ 0.05319386 -0.05319386] [-4.45789156e-05  4.45789156e-05] [-1.57563251e-06  1.57563251e-06] -0.011651679507615854 [6.81808683 7.96926541]
[6.81800765 7.96927491]
[128.07965219 -21.54653288] [ 2.75077031 -2.75077031] [-0.00187507  0.00187507] [ 0.05319229 -0.05319229] [-4.45776493e-05  4.45776493e-05] [-1.60732127e-06  1.60732127e-06] -0.011651715040786445 [6.81800765 7.96927491]
[6.81792678 7.96928441]
[128.07777713 -21.54465781] [ 2.8039626 -2.8039626] [-0.00191964  0.00191964] [ 0.05319068 -0.05319068] [-4.45763687e-05  4.45763687e-05] [-1.63900926e-06  1.63900926e-06] -0.01165175194499076 [6.81792678 7.96928441]
[6.81784422 7.9692939 ]
[128.07585748 -21.54273817]

[127.65264451 -21.11952519] [ 8.21553143 -8.21553143] [-0.00645728  0.00645728] [ 0.05286038 -0.05286038] [-4.43696068e-05  4.43696068e-05] [-4.86842492e-06  4.86842492e-06] -0.011662731862706353 [6.8008173  7.97025338]
[6.80056273 7.97026289]
[127.64618723 -21.11306792] [ 8.26839181 -8.26839181] [-0.00650164  0.00650164] [ 0.05285551 -0.05285551] [-4.43668307e-05  4.43668307e-05] [-4.90007094e-06  4.90007094e-06] -0.011662910462842058 [6.80056273 7.97026289]
[6.80030647 7.9702724 ]
[127.63968559 -21.10656627] [ 8.32124732 -8.32124732] [-0.00654601  0.00654601] [ 0.05285061 -0.05285061] [-4.43640401e-05  4.43640401e-05] [-4.93171689e-06  4.93171689e-06] -0.011663090446357754 [6.80030647 7.9702724 ]
[6.80004853 7.97028191]
[127.63313958 -21.10002026] [ 8.37409793 -8.37409793] [-0.00659038  0.00659038] [ 0.05284568 -0.05284568] [-4.43612348e-05  4.43612348e-05] [-4.9633628e-06  4.9633628e-06] -0.011663271813460104 [6.80004853 7.97028191]
[6.7997889  7.97029141]
[127.6265492  -21.09342989

[6.77034063 7.97112937]
[126.87323363 -20.34011432] [ 13.05433293 -13.05433293] [-0.01052581  0.01052581] [ 0.05228 -0.05228] [-4.40526093e-05  4.40526093e-05] [-7.78044208e-06  7.78044208e-06] -0.011684984613914007 [6.77034063 7.97112937]
[6.76993097 7.97113891]
[126.86270782 -20.3295885 ] [ 13.10661294 -13.10661294] [-0.01056987  0.01056987] [ 0.05227222 -0.05227222] [-4.40484738e-05  4.40484738e-05] [-7.81211011e-06  7.81211011e-06] -0.011685291564355417 [6.76993097 7.97113891]
[6.76951961 7.97114845]
[126.85213795 -20.31901864] [ 13.15888516 -13.15888516] [-0.01061392  0.01061392] [ 0.05226441 -0.05226441] [-4.40443233e-05  4.40443233e-05] [-7.84377868e-06  7.84377868e-06] -0.011685599924357016 [6.76951961 7.97114845]
[6.76910657 7.97115799]
[126.84152404 -20.30840472] [ 13.21114957 -13.21114957] [-0.01065796  0.01065796] [ 0.05225657 -0.05225657] [-4.40401578e-05  4.40401578e-05] [-7.87544778e-06  7.87544778e-06] -0.01168590969428416 [6.76910657 7.97115799]
[6.76869184 7.97116753]

[125.67720682 -19.14408751] [ 17.98180824 -17.98180824] [-0.01469026  0.01469026] [ 0.05139937 -0.05139937] [-4.35920736e-05  4.35920736e-05] [-1.07921307e-05  1.07921307e-05] -0.011720494854900895 [6.72388672 7.97203813]
[6.72331666 7.97204773]
[125.66251657 -19.12939725] [ 18.03320761 -18.03320761] [-0.01473385  0.01473385] [ 0.05138858 -0.05138858] [-4.35864888e-05  4.35864888e-05] [-1.08238763e-05  1.08238763e-05] -0.011720937593168815 [6.72331666 7.97204773]
[6.7227449  7.97205733]
[125.64778272 -19.1146634 ] [ 18.08459619 -18.08459619] [-0.01477743  0.01477743] [ 0.05137775 -0.05137775] [-4.35808885e-05  4.35808885e-05] [-1.08556229e-05  1.08556229e-05] -0.01172138178376037 [6.7227449  7.97205733]
[6.72217146 7.97206693]
[125.63300528 -19.09988597] [ 18.13597395 -18.13597395] [-0.01482102  0.01482102] [ 0.0513669 -0.0513669] [-4.35752726e-05  4.35752726e-05] [-1.08873707e-05  1.08873707e-05] -0.011721827427214306 [6.72217146 7.97206693]
[6.72159633 7.97207653]
[125.61818427 -19.0

In [46]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(title="dt=1, Euler Method, Two ellipse produce two circles, e=0.5", plot_width=400, plot_height=400, y_range=[-150,150],x_range=[-150,150])
t = np.linspace(0, 2*math.pi, 100)
focusx=getfocus(0.5*rad0,ecc0)
b=0.5*rad0*(1+ecc)
print(b)
print(focusx)
p.line(xcoord1,ycoord1, line_color="purple",legend="Ellipse 1")
p.line(xcoord2,ycoord2, line_color="blue",legend="Ellipse 2")
p.line(-focusx+rad0*(1+ecc0)*np.cos(t),rad0*np.sin(t), line_color="green", legend="Ideal ellipse")
p.legend.location = "bottom_left"
p.legend.click_policy="hide"

show(p) # show the results

Loading BokehJS ...

75.0
41.53311931459037


I don't know why it's producing circles offset from eachother, rather than ellipses with eccentricities of 0.5.

In [47]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(title="Energy", plot_width=400, plot_height=400)
p.line(tarr,Earr, line_color="purple",legend="Energy")
p.legend.location = "bottom_left"
p.legend.click_policy="hide"

show(p) # show the results

Loading BokehJS ...

In [49]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(title="Angular Momentum", plot_width=400, plot_height=400)
p.line(tarr,Larr,line_color="purple", legend="Angular Momentum")
p.legend.location = "bottom_left"
p.legend.click_policy="hide"

show(p) # show the results

Loading BokehJS ...

In [38]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
xmomentum=np.array(vxarr1)+np.array(vxarr2)
p = figure(title="X linear momentum", plot_width=400, plot_height=400)
p.triangle(tarr,xmomentum, size=1, line_color="purple",fill_color="purple", fill_alpha=0.5, legend="X linear momentum")
p.legend.location = "bottom_left"
p.legend.click_policy="hide"

show(p) # show the results 

Loading BokehJS ...

In [27]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
ymomentum=np.array(vyarr1)+np.array(vyarr2)
p = figure(title="Y linear momentum", plot_width=400, plot_height=400)
p.triangle(tarr,xmomentum, size=1, line_color="purple",fill_color="purple", fill_alpha=0.5, legend="Y linear momentum")
p.legend.location = "bottom_left"
p.legend.click_policy="hide"

show(p) # show the results 

Loading BokehJS ...

In [ ]:
Linear momentum, angular momentum, and energy should be constant. Linear momentum in both x and y are, and appear to be zero as expected. Angular momentum should be nonzero, but is not expected to grow or shrink over the course of the orbit and is not expected to grow linearly over time. There is definitely a problem. 